# Setup

In [1]:
from Data.data_dicts import character_dict, source_dict, random_state

In [2]:
# Mount google drive
import os
try:
    import google.colab
    IN_COLAB = True
except:
    IN_COLAB = False
    os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"

if IN_COLAB:
    from google.colab import drive
    drive.mount('/content/drive',force_remount=True)
    base_folder = '/content/drive/My Drive/unibo/NLP_project/BarneyBot'
    # Install dependencies
    os.system("pip install datasets")
    os.system("pip install transformers")
    os.system("pip install rouge_score")
    os.system("pip install -U sentence-transformers")
else:
    base_folder = os.getcwd()

# Set metrics folder for inputs
in_metrics_folder = os.path.join(base_folder, 'Metrics')
if not os.path.exists(in_metrics_folder):
    os.makedirs(in_metrics_folder)

# Set metrics folder for outputs
out_metrics_folder = os.path.join(base_folder, 'Metrics', 'New')
if not os.path.exists(out_metrics_folder):
    os.makedirs(out_metrics_folder)

In [3]:
# Import for general utilities
import pandas as pd
import tensorflow as tf
import json
import numpy as np
import time
import scipy as sp
from datasets import load_dataset, DatasetDict
from tqdm import tqdm 
from matplotlib import pyplot as plt
%matplotlib inline
from itertools import product as zip_cartesian

In [4]:
# Import BBRadar for plot a radar plot for Emotion metric 
from Lib.BBRadar import BBRadar
import pprint
printer = pprint.PrettyPrinter(depth=4, width=100)

In [5]:
def load_df(character):
    # Builds the path where the dataset is stored
    dataset_path = os.path.join(base_folder, "Data", "Characters", character, character+'.csv')
    
    # Loads the datasat of the character `character`
    character_hg = load_dataset('csv', 
                                data_files=dataset_path, 
                                cache_dir=os.path.join(base_folder, "cache"))
    
    # 85% train / 10% test / 5% validation
    train_test_hg = character_hg['train'].train_test_split(test_size=0.15, seed=random_state)
    test_val = train_test_hg['test'].train_test_split(test_size=0.33, seed=random_state)
    
    # This gives a name to three splits of the dataset
    character_hg = DatasetDict({
        'train': train_test_hg['train'],
        'test': test_val['train'],
        'val': test_val['test']
    })
    
    return character_hg

# Metric Querying Function Definition

In [6]:
from enum import Enum
import logging
logging.getLogger('datasets').setLevel(51)

class MetricDependency(int, Enum):
    DATASET = 0      # Metric depends on datasets only and/or base DialoGPT model
    COHERENT = 1     # Metric depends on chatbot trained on its dataset
    ADVERSARIAL = 2  # Metric depends on chatbot trained on a dataset but with another dataset of reference
    COMPARATIVE = 3  # Metric depends on comparison between chatbots

class MetricArity(int, Enum):
    SINGLE = 1
    PAIRWISE = 2

class MetricDeterminism(int, Enum):
    DETERMINISTIC = 0 # There is a closed-form equation for this metric, which is fully computed
    PROBABILISTIC = 1 # The metric is obtained through explainable approx., e.g. SGD, partial computation on a subset...
    NEURAL = 2        # The metric is obtained via a neural network
    HUMAN = 4         # The metric is obtained via human surveying

class MetricActor(int, Enum):
    DATASET_CHARCONTEXT = 0     # any character but not 'Default', including "Common"
    DATASET_CHAR = 1   # any character but not 'Default', including "Common"
    DIALOGPT_GREEDY = 10  # any character including 'Base'
    DIALOGPT_NBEAMS = 11  # any character including 'Base'
    DIALOGPT_SAMPLE = 12  # any character including 'Base'
    
characters_hg = {c:None for c in character_dict.keys()}

def is_character(char):
    if char in character_dict.keys() and char != 'Default':
        return True
    elif char == 'Base' or char == 'Common':
        return False
    else:
        logging.error("Unknown character name " + char + "!")

In [7]:
charlist = ['Barney', 'Bender', 'Fry', 'Harry', 'Joey', 'Phoebe', 'Sheldon', 'Vader']
debug_check = {
    'bleu': set(),
    'rouge l': set(),
    'semantic similarity': set(),
    'semantic answer similarity': set(),
    'perplexity': set(),
    'distinct': set(),
    'emotion': set(),
    'semantic classifier': set()
}

def read_from_oldfile(base_path, metric_name, filename, subfile, metric_id):
    try:
        metric_path = os.path.join(base_path, filename)
        # Open and read the file
        with open(metric_path, 'r') as file:
            json_string = file.read()
        metrics = json.loads(json_string)
        if subfile != None:
            metrics = metrics[subfile]
        # Extract appropriate metric
        if metric_id != None:
            metric = metrics[metric_name][metric_id]
        else:
            metric = metrics[metric_name]
        return metric
    except:
        raise Exception("Unsupported parameters in loading metrics file!")
        
def read_from_oldfile_sentencepair_metrics(base_path, chars, gentypes, metric_name):
    # Sentencepair metrics are Bleu, Rouge-L, Semantic Similarity, Semantic Answer Similarity
    filename = None
    if is_character(chars[0]) and is_character(chars[1]) and chars[0] == chars[1]:
        if gentypes[0] == MetricActor.DATASET_CHARCONTEXT and gentypes[1] == MetricActor.DATASET_CHAR:
            filename = chars[0] + '_base_metrics.json'
            metric_id = 0
            subfile = None
            debug_check[metric_name].add("A")
        elif gentypes[0] == MetricActor.DATASET_CHARCONTEXT and gentypes[1] == MetricActor.DIALOGPT_GREEDY:
            filename = chars[0] + '_base_metrics.json'
            metric_id = 1
            subfile = None
            debug_check[metric_name].add("B")
        elif gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_GREEDY:
            filename = chars[0] + '_base_metrics.json'
            metric_id = 2
            subfile = None
            debug_check[metric_name].add("C")
        elif gentypes[0] == MetricActor.DATASET_CHARCONTEXT and gentypes[1] == MetricActor.DIALOGPT_NBEAMS:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 1
            subfile = 'greedy_vs_nbeams'
            debug_check[metric_name].add("D")
        elif gentypes[0] == MetricActor.DIALOGPT_GREEDY and gentypes[1] == MetricActor.DIALOGPT_NBEAMS:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 2
            subfile = 'greedy_vs_nbeams'
            debug_check[metric_name].add("E")
        elif gentypes[0] == MetricActor.DATASET_CHARCONTEXT and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 1
            subfile = 'greedy_vs_sampling'
            debug_check[metric_name].add("F")
        elif gentypes[0] == MetricActor.DIALOGPT_GREEDY and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 2
            subfile = 'greedy_vs_sampling'
            debug_check[metric_name].add("G")
        elif gentypes[0] == MetricActor.DIALOGPT_NBEAMS and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 2
            subfile = 'nbeams_vs_sampling'
            debug_check[metric_name].add("H")
        if gentypes[0] == MetricActor.DATASET_CHARCONTEXT and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_vs_nonfinetuned_metrics.json'
            metric_id = 0
            subfile = None
            debug_check[metric_name].add("I")
    elif is_character(chars[0]) and chars[1] == 'Base':
        if gentypes[0] == MetricActor.DATASET_CHARCONTEXT and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_vs_nonfinetuned_metrics.json'
            metric_id = 1
            subfile = None
            debug_check[metric_name].add("L")
        elif gentypes[0] == MetricActor.DIALOGPT_SAMPLE and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_vs_nonfinetuned_metrics.json'
            metric_id = 2
            subfile = None
            debug_check[metric_name].add("M")
    elif is_character(chars[0]) and is_character(chars[1]) and chars[0] != chars[1]:         
        if gentypes[0] == MetricActor.DIALOGPT_SAMPLE and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_vs_' + chars[1] + '_metrics.json'
            metric_id = 2
            subfile = None
            debug_check[metric_name].add("N")
    elif chars[0] == 'Common' and is_character(chars[1]):
        if gentypes[0] == MetricActor.DATASET_CHARCONTEXT and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            for char in charlist:
                if os.path.exists(os.path.join(in_metrics_folder, chars[1] + '_vs_' + char + '_metrics.json')):
                    filename = chars[1] + '_vs_' + char + '_metrics.json'
                    metric_id = 0
                    debug_check[metric_name].add("O")
                    break
                elif os.path.exists(os.path.join(in_metrics_folder, char + '_vs_' + chars[1] + '_metrics.json')):
                    filename = char + '_vs_' + chars[1] + '_metrics.json'
                    metric_id = 1
                    debug_check[metric_name].add("P")
                    break
            subfile = None
    if filename == None:
        raise Exception("Unsupported parameters in loading metrics file!")
    return read_from_oldfile(base_path, metric_name, filename, subfile, metric_id)
        
def read_from_oldfile_perplexity(base_path, chars, gentypes):
    metric_name = 'perplexity'
    filename = None
    if is_character(chars[0]) and is_character(chars[1]) and chars[0] == chars[1]:
        if gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_GREEDY:
            filename = chars[0] + '_base_metrics.json'
            metric_id = None
            subfile = None
            debug_check[metric_name].add("A")
    elif is_character(chars[0]) and chars[1] == 'Base':
        if gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_vs_nonfinetuned_metrics.json'
            metric_id = 1
            subfile = None
            debug_check[metric_name].add("B")
    elif chars[0] == 'Common' and is_character(chars[1]):
        if gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            for char in charlist:
                if os.path.exists(os.path.join(in_metrics_folder, chars[1] + '_vs_' + char + '_metrics.json')):
                    filename = chars[1] + '_vs_' + char + '_metrics.json'
                    metric_id = 0
                    debug_check[metric_name].add("C")
                    break
                elif os.path.exists(os.path.join(in_metrics_folder, char + '_vs_' + chars[1] + '_metrics.json')):
                    filename = char + '_vs_' + chars[1] + '_metrics.json'
                    metric_id = 1
                    debug_check[metric_name].add("D")
                    break
            subfile = None
    if filename == None:
        raise Exception("Unsupported parameters in loading metrics file!")
    return read_from_oldfile(base_path, metric_name, filename, subfile, metric_id)

def read_from_oldfile_chclassifier(base_path, chars, gentypes):
    metric_name = "semantic classifier"
    filename = None
    if is_character(chars[0]) and is_character(chars[1]) and chars[0] == chars[1]:
        if gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DATASET_CHAR:
            filename = chars[0] + '_base_metrics.json'
            metric_id = 0
            subfile = None
            debug_check[metric_name].add("A")
        elif gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_GREEDY:
            filename = chars[0] + '_base_metrics.json'
            metric_id = 1
            subfile = None
            debug_check[metric_name].add("B")
        elif gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_NBEAMS:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 1
            subfile = 'greedy_vs_nbeams'
            debug_check[metric_name].add("C")
        elif gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 1
            subfile = 'nbeams_vs_sampling'
            debug_check[metric_name].add("D")
    elif is_character(chars[0]) and chars[1] == 'Base':
        if gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_vs_nonfinetuned_metrics.json'
            metric_id = 1
            subfile = None
            debug_check[metric_name].add("E")
    elif is_character(chars[0]) and is_character(chars[1]) and chars[0] != chars[1]:         
        if gentypes[0] == MetricActor.DATASET_CHAR and gentypes[1] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_vs_' + chars[1] + '_metrics.json'
            metric_id = 2
            subfile = None
            debug_check[metric_name].add("F")
    if filename == None:
        raise Exception("Unsupported parameters in loading metrics file!")
    return read_from_oldfile(base_path, metric_name, filename, subfile, metric_id)    

def read_from_oldfile_single_metrics(base_path, chars, gentypes, metric_name):
    # Single metrics are distinct, emotion classifier
    if metric_name == "emotion classifier":
        metric_name = "emotion"
    filename = None
    if is_character(chars[0]):
        if gentypes[0] == MetricActor.DATASET_CHARCONTEXT:
            filename = chars[0] + '_base_metrics.json'
            metric_id = 0
            subfile = None
            debug_check[metric_name].add("A")
        elif gentypes[0] == MetricActor.DATASET_CHAR:
            filename = chars[0] + '_base_metrics.json'
            metric_id = 1
            subfile = None            
            debug_check[metric_name].add("B")
        elif gentypes[0] == MetricActor.DIALOGPT_GREEDY:
            filename = chars[0] + '_base_metrics.json'
            metric_id = 2
            subfile = None
            debug_check[metric_name].add("C")
        elif gentypes[0] == MetricActor.DIALOGPT_NBEAMS:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 2
            subfile = 'greedy_vs_nbeams'      
            debug_check[metric_name].add("D")
        elif gentypes[0] == MetricActor.DIALOGPT_SAMPLE:
            filename = chars[0] + '_sampling_comparison_metrics.json'
            metric_id = 2
            subfile = 'greedy_vs_sampling'
            debug_check[metric_name].add("E")
    elif chars[0] == 'Base':
        if gentypes[0] == MetricActor.DIALOGPT_SAMPLE:
            filename = 'Barney' + '_vs_nonfinetuned_metrics.json'
            metric_id = 2
            subfile = None
            debug_check[metric_name].add("F")
    elif chars[0] == 'Common':
        if gentypes[0] == MetricActor.DATASET_CHARCONTEXT:
            filename = 'Barney' + '_vs_' + 'Harry' + '_metrics.json'
            metric_id = 0
            subfile = None
            debug_check[metric_name].add("G")
    if filename == None:
        raise Exception("Unsupported parameters in loading metrics file!")
    return read_from_oldfile(base_path, metric_name, filename, subfile, metric_id) 

In [14]:
def get_metrics_list():
    return ['bleu', 'rouge l', 'semantic similarity', 'semantic answer similarity', 'chatbot classifier', 'emotion classifier',
           'distinct', 'perplexity']

def get_metric_args(metric_name):
    if metric_name == 'bleu' or metric_name == 'semantic answer similarity' or metric_name == 'rouge l':
        return {
            'metric_actors': ['predictor', 'reference'],
            'metric_params': []
        }
    elif metric_name == 'semantic similarity':
        return {
            'metric_actors': ['document0', 'document1'],
            'metric_params': []
        }
    elif metric_name == 'perplexity':
        return {
            'metric_actors': ['predictor', 'training_set'],
            'metric_params': []
        }
    elif metric_name == 'chatbot classifier':
        return {
            'metric_actors': ['document', 'training_set'],
            'metric_params': []
        }
    elif metric_name == 'distinct' or metric_name == 'emotion classifier':
        return {
            'metric_actors': ['document'],
            'metric_params': []
        }
    else:
        raise Exception("Unsupported or unknown metric name!")

# TO IMPLEMENT: perplexity, distinct, emotion, semantic classifier
def fetch_old_metrics(what):
    # If input is not a list, make it so, with a single element
    if not isinstance(what, list):
        what = [what]
    
    answers = list()
    # Iterate over queries
    for query in what:
        skip = False
        # Fetch inputs
        metric_name = query['metric_name'] # 'lines_count' | 'bleu' | 'semantic similarity' | 'rouge l' | 'semantic answer similarity'
        metric_actors = query['metric_actors'] # dict of (MetricActor, string), with string compatible for the actor type
        metric_params = query['metric_params'] # parameters specific to metric
        
        if metric_name == 'lines count':
            if bool(metric_params):
                metric_params = dict()
                logging.warning("Metric parameters are incompatible with metric type. Defaulting parameters on output to " + 
                              str(metric_params) + ".")
            if not set(metric_actors.keys()).issubset(['document']):
                logging.warning("Unexpected metric actors! Ignoring.")
            if not set(['document']).issubset(set(metric_actors.keys())):
                logging.error("Missing metric actors! Required actors are ['document']!") 
            if metric_actors['document'][0] != MetricActor.DATASET_CHAR:
                logging.error("Invalid actor type for metric actor 'document'!")
            char = metric_actors['document'][1]
            if characters_hg[char] == None:
                characters_hg[char] = load_df(char)
            sets = [s for s in characters_hg[char]]
            answer = {s: len(characters_hg[char][s]) for s in sets}
            metric_dependency = MetricDependency.DATASET
            metric_arity = MetricArity.SINGLE
            metric_samples = 1
            metric_determinism = MetricDeterminism.DETERMINISTIC
            
        elif metric_name == 'bleu' or metric_name == 'rouge l' or metric_name == 'semantic answer similarity':
            if bool(metric_params):
                metric_params = dict()
                logging.warning("Metric parameters are incompatible with metric type. Defaulting parameters on output to " + 
                              str(metric_params) + ".")
            if not set(metric_actors.keys()).issubset(['predictor', 'reference']):
                logging.warning("Unexpected metric actors! Ignoring.")
            if not set(['predictor', 'reference']).issubset(set(metric_actors.keys())):
                logging.error("Missing metric actors! Required actors are ['predictor', 'reference']!")   
            
            try:
                answer = read_from_oldfile_sentencepair_metrics(in_metrics_folder,
                                          [metric_actors['reference'][1], metric_actors['predictor'][1]],
                                          [metric_actors['reference'][0], metric_actors['predictor'][0]],
                                          metric_name)
            except:
                logging.error("Metric could not be read! For query:\n" + str(query) + "\nSkipping.")
                skip = True
            actor_types = [t[0] for t in metric_actors.values()]
            if all(at.value < 10 for at in actor_types):
                metric_dependency = MetricDependency.DATASET
            elif metric_actors['reference'][0].value < 10 and metric_actors['predictor'][1] == 'Base':
                metric_dependency = MetricDependency.DATASET
            elif metric_actors['reference'][1] == metric_actors['predictor'][1]:
                metric_dependency = MetricDependency.COHERENT
            elif all(at.value >= 10 for at in actor_types):
                metric_dependency = MetricDependency.COMPARATIVE
            else:
                metric_dependency = MetricDependency.ADVERSARIAL
            metric_arity = MetricArity.PAIRWISE
            metric_samples = "Unknown"
            if metric_name == 'bleu' or metric_name == 'rouge l':
                metric_determinism = MetricDeterminism.DETERMINISTIC
            elif metric_name == 'semantic answer similarity':
                metric_determinism = MetricDeterminism.NEURAL
            
        elif metric_name == 'semantic similarity':
            if bool(metric_params):
                metric_params = dict()
                logging.warning("Metric parameters are incompatible with metric type. Defaulting parameters on output to " + 
                              str(metric_params) + ".")
            if not set(metric_actors.keys()).issubset(['document0', 'document1']):
                logging.warning("Unexpected metric actors! Ignoring.")
            if not set(['document0', 'document1']).issubset(set(metric_actors.keys())):
                logging.error("Missing metric actors! Required actors are ['document0', 'document1']!")   
            try:
                answer = read_from_oldfile_sentencepair_metrics(in_metrics_folder,
                                          [metric_actors['document0'][1], metric_actors['document1'][1]],
                                          [metric_actors['document0'][0], metric_actors['document1'][0]],
                                          metric_name)
            except:
                try:
                    answer = read_from_oldfile_sentencepair_metrics(in_metrics_folder,
                                              [metric_actors['document1'][1], metric_actors['document0'][1]],
                                              [metric_actors['document1'][0], metric_actors['document0'][0]],
                                              metric_name)  
                except:
                    logging.error("Metric could not be read! For query:\n" + str(query) + "\nSkipping.")
                    skip = True
            actor_types = [t[0] for t in metric_actors.values()]
            if all(at.value < 10 for at in actor_types):
                metric_dependency = MetricDependency.DATASET
            elif (metric_actors['document1'][0].value < 10 and metric_actors['document0'][1] == 'Base') or \
                 (metric_actors['document0'][0].value < 10 and metric_actors['document1'][1] == 'Base'):
                metric_dependency = MetricDependency.DATASET
            elif metric_actors['document1'][1] == metric_actors['document0'][1]:
                metric_dependency = MetricDependency.COHERENT
            elif all(at.value >= 10 for at in actor_types):
                metric_dependency = MetricDependency.COMPARATIVE
            else:
                metric_dependency = MetricDependency.ADVERSARIAL
            metric_arity = MetricArity.PAIRWISE
            metric_samples = "Unknown"
            metric_determinism = MetricDeterminism.NEURAL
        elif metric_name == 'perplexity':
            if bool(metric_params):
                metric_params = dict()
                logging.warning("Metric parameters are incompatible with metric type. Defaulting parameters on output to " + 
                              str(metric_params) + ".")
            if not set(metric_actors.keys()).issubset(['training_set', 'predictor']):
                logging.warning("Unexpected metric actors! Ignoring.")
            if not set(['training_set', 'predictor']).issubset(set(metric_actors.keys())):
                logging.error("Missing metric actors! Required actors are ['training_set', 'predictor']!")
            if metric_actors['training_set'][0] != MetricActor.DATASET_CHAR:
                logging.error("Invalid actor type for metric actor 'training_set'!")
            if metric_actors['predictor'][0].value < 10:
                logging.error("Invalid actor type for metric actor 'predictor'!")
            try:
                answer = read_from_oldfile_perplexity(in_metrics_folder,
                                          [metric_actors['training_set'][1], metric_actors['predictor'][1]],
                                          [metric_actors['training_set'][0], metric_actors['predictor'][0]])
            except:
                logging.error("Metric could not be read! For query:\n" + str(query) + "\nSkipping.")
                skip = True
            if metric_actors['predictor'][0].value < 10:
                metric_dependency = MetricDependency.DATASET
            elif metric_actors['predictor'][1] == 'Base':
                metric_dependency = MetricDependency.DATASET
            elif metric_actors['training_set'][1] == metric_actors['predictor'][1]:
                metric_dependency = MetricDependency.COHERENT
            else:
                metric_dependency = MetricDependency.ADVERSARIAL
            metric_arity = MetricArity.PAIRWISE
            metric_samples = "Unknown"
            metric_determinism = MetricDeterminism.DETERMINISTIC
        elif metric_name == 'chatbot classifier':
            if not set(metric_actors.keys()).issubset(['training_set', 'document']):
                logging.warning("Unexpected metric actors! Ignoring.")
            if not set(['training_set', 'document']).issubset(set(metric_actors.keys())):
                logging.error("Missing metric actors! Required actors are ['training_set', 'document']!")
            if metric_actors['training_set'][0] != MetricActor.DATASET_CHAR:
                logging.error("Invalid actor type for metric actor 'training_set'!")
            try:
                answer = read_from_oldfile_chclassifier(in_metrics_folder,
                                          [metric_actors['training_set'][1], metric_actors['document'][1]],
                                          [metric_actors['training_set'][0], metric_actors['document'][0]])
            except:
                logging.error("Metric could not be read! For query:\n" + str(query) + "\nSkipping.")
                skip = True
            if metric_actors['document'][0].value < 10:
                metric_dependency = MetricDependency.DATASET
            elif metric_actors['document'][1] == 'Base':
                metric_dependency = MetricDependency.DATASET
            elif metric_actors['training_set'][1] == metric_actors['document'][1]:
                metric_dependency = MetricDependency.COHERENT
            else:
                metric_dependency = MetricDependency.ADVERSARIAL
            metric_arity = MetricArity.PAIRWISE
            metric_samples = "Unknown"
            metric_determinism = MetricDeterminism.PROBABILISTIC
        elif metric_name == 'distinct' or metric_name == 'emotion classifier':
            if not set(metric_actors.keys()).issubset(['document']):
                logging.warning("Unexpected metric actors! Ignoring.")
            if not set(['document']).issubset(set(metric_actors.keys())):
                logging.error("Missing metric actors! Required actors are ['document']!")
            try:
                answer = read_from_oldfile_single_metrics(in_metrics_folder,
                                          [metric_actors['document'][1]],
                                          [metric_actors['document'][0]],
                                          metric_name)
            except:
                logging.error("Metric could not be read! For query:\n" + str(query) + "\nSkipping.")
                skip = True
            if metric_actors['document'][0].value < 10:
                metric_dependency = MetricDependency.DATASET
            elif metric_actors['document'][1] == 'Base':
                metric_dependency = MetricDependency.DATASET
            else:
                metric_dependency = MetricDependency.COHERENT
            metric_arity = MetricArity.SINGLE
            metric_samples = "Unknown"
            if metric_name == 'distinct':
                metric_determinism = MetricDeterminism.DETERMINISTIC
            elif metric_name == 'emotion classifier':
                metric_determinism = MetricDeterminism.NEURAL
        else:
            logging.error("Metric name not found!")
        
        if not skip:
            return_data = {
                'metric_name': metric_name,
                'metric_version': 1,
                'metric_attempt': 0,
                'metric_dependency': metric_dependency,
                'metric_actors': metric_actors,
                'context': {
                    'dialogpt_size': 'small',
                    'dialogpt_context_sentences': 5,
                    'dialogpt_nbeams_beams': 3,
                    'dialogpt_sample_top_p': 0.92,
                    'dialogpt_sample_top_k': 50
                },
                'metric_params': metric_params,
                'metric_arity': metric_arity,
                'metric_samples': metric_samples,
                'metric_determinism': metric_determinism,
                'answer': answer
            }
            answers.append(return_data)
    return answers

# Metric Retrieval

In [15]:
from typing import Dict, Any
import hashlib
import json

def dict_hash(dictionary: Dict[str, Any]) -> str:
    dhash = hashlib.md5()
    encoded = json.dumps(dictionary, sort_keys=True).encode()
    dhash.update(encoded)
    return dhash.hexdigest()

In [16]:
# Store a json file
def save_as_json(filepath, filename, data):
    if not os.path.exists(filepath):
        os.makedirs(filepath, exist_ok=True)
    with open(os.path.join(filepath, filename + ".json"), 'w') as f:
        f.write(json.dumps(data, indent=4))

# Load a json file
def load_from_json(filepath, filename):
    if not os.path.exists(os.path.join(filepath, filename + '.json')):
        return dict()
    with open(os.path.join(filepath, filename + '.json'), 'r') as f:
        return json.load(f)

In [74]:
'''
what = {
    'metric_name': 'perplexity', # Fetch me the chatbot classifier value
    'metric_actors': {
        'training_set': (MetricActor.DATASET_CHAR, 'Barney'),        # between the Barney dataset label sentences
        'predictor': (MetricActor.DIALOGPT_SAMPLE, 'Harry') 
    },
    'metric_params': {} # No additional params for this metric
}

printer.pprint(fetch_old_metrics(what)) # Also returns some further metric characteristics
'''

"\nwhat = {\n    'metric_name': 'perplexity', # Fetch me the chatbot classifier value\n    'metric_actors': {\n        'training_set': (MetricActor.DATASET_CHAR, 'Barney'),        # between the Barney dataset label sentences\n        'predictor': (MetricActor.DIALOGPT_SAMPLE, 'Harry') \n    },\n    'metric_params': {} # No additional params for this metric\n}\n\nprinter.pprint(fetch_old_metrics(what)) # Also returns some further metric characteristics\n"

# Save Line Counts Metric

In [45]:
linecounts = [{
    'metric_name': 'lines count',
    'metric_actors': {
        'document': (MetricActor.DATASET_CHAR, char)
    },
    'metric_params': {} 
} for char in ['Barney', 'Bender', 'Fry', 'Harry', 'Joey', 'Phoebe', 'Sheldon', 'Vader']]

linecounts = fetch_old_metrics(linecounts)

for i in range(len(linecounts)):
    linecounts[i]['hash'] = dict_hash({key: linecounts[i][key] for key in ['metric_name',
                                                                           'metric_version',
                                                                           'metric_attempt',
                                                                           'metric_actors', 
                                                                           'context',
                                                                           'metric_params',
                                                                           'metric_samples']})
save_as_json(out_metrics_folder, 'Line Count', linecounts)

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

# Save Single Metrics

In [122]:
for metric in [('emotion classifier', 'Emotion Classifier'), ('distinct', 'Distinct')]:
    print("Saving metric " + metric[1])
    query = [{
        'metric_name': metric[0],
        'metric_actors': {
            'document': (doc, char)
        },
        'metric_params': {} 
    } for doc in [MetricActor.DATASET_CHARCONTEXT, MetricActor.DATASET_CHAR, MetricActor.DIALOGPT_GREEDY,
                  MetricActor.DIALOGPT_NBEAMS, MetricActor.DIALOGPT_SAMPLE]
      for char in ['Barney', 'Bender', 'Fry', 'Harry', 'Joey', 'Phoebe', 'Sheldon', 'Vader',
                   'Common' if doc.value < 10 else 'Base']]

    answer = fetch_old_metrics(query)

    for i in range(len(answer)):
        answer[i]['hash'] = dict_hash({key: answer[i][key] for key in ['metric_name',
                                                                       'metric_version',
                                                                       'metric_attempt',
                                                                       'metric_actors', 
                                                                       'context',
                                                                       'metric_params',
                                                                       'metric_samples']})
    save_as_json(out_metrics_folder, metric[1], answer)

ERROR:root:Metric could not be read! For query:
{'metric_name': 'emotion classifier', 'metric_actors': {'document': (<MetricActor.DATASET_CHAR: 1>, 'Common')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'emotion classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Base')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'emotion classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Base')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'distinct', 'metric_actors': {'document': (<MetricActor.DATASET_CHAR: 1>, 'Common')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'distinct', 'metric_actors': {'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Base')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_na

Saving metric Emotion Classifier
Saving metric Distinct


In [123]:
print(debug_check)

{'bleu': set(), 'rouge l': set(), 'semantic similarity': set(), 'semantic answer similarity': set(), 'perplexity': set(), 'distinct': {'E', 'A', 'C', 'B', 'G', 'D', 'F'}, 'emotion': {'E', 'A', 'C', 'B', 'G', 'D', 'F'}, 'semantic classifier': set()}


# Save Pairwise Metrics

In [137]:
for metric in [
    ('bleu', 'BLEU', 'predictor', 'reference'),
    ('rouge l', 'ROUGE-L', 'predictor', 'reference'),
    ('semantic similarity', 'Semantic Similarity', 'document0', 'document1'),
    ('semantic answer similarity', 'Semantic Answer Similarity', 'predictor', 'reference'),
    ('perplexity', 'Perplexity', 'training_set', 'predictor')
]:
    print("Saving metric " + metric[1])
    query = [{
        'metric_name': metric[0],
        'metric_actors': {
            metric[2]: (doc, char),
            metric[3]: (doc2, char2)
        },
        'metric_params': {} 
    } for doc in [MetricActor.DATASET_CHARCONTEXT, MetricActor.DATASET_CHAR, MetricActor.DIALOGPT_GREEDY,
                  MetricActor.DIALOGPT_NBEAMS, MetricActor.DIALOGPT_SAMPLE]
      for char in ['Barney', 'Bender', 'Fry', 'Harry', 'Joey', 'Phoebe', 'Sheldon', 'Vader',
                   'Common' if doc.value < 10 else 'Base']
      for doc2 in [MetricActor.DATASET_CHARCONTEXT, MetricActor.DATASET_CHAR, MetricActor.DIALOGPT_GREEDY,
                  MetricActor.DIALOGPT_NBEAMS, MetricActor.DIALOGPT_SAMPLE]
      for char2 in ['Barney', 'Bender', 'Fry', 'Harry', 'Joey', 'Phoebe', 'Sheldon', 'Vader',
                   'Common' if doc2.value < 10 else 'Base']]

    answer = fetch_old_metrics(query)
    logging.error("Found " + str(len(answer)) + " metrics for " + str(metric[1]))
    
    for i in range(len(answer)):
        answer[i]['hash'] = dict_hash({key: answer[i][key] for key in ['metric_name',
                                                                       'metric_version',
                                                                       'metric_attempt',
                                                                       'metric_actors', 
                                                                       'context',
                                                                       'metric_params',
                                                                       'metric_samples']})
    save_as_json(out_metrics_folder, metric[1], answer)

ERROR:root:Found 24 metrics for BLEU
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'reference': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'reference': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'reference': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'reference': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Harry')}, 'metri

ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'reference': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Vader')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'reference': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Base')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'reference': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Barney')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'reference': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Bender')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could

ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'reference': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Phoebe')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'reference': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Sheldon')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'reference': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Vader')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'reference': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Base')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric coul

ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry'), 'reference': (<MetricActor.DATASET_CHAR: 1>, 'Harry')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry'), 'reference': (<MetricActor.DATASET_CHAR: 1>, 'Joey')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry'), 'reference': (<MetricActor.DATASET_CHAR: 1>, 'Phoebe')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry'), 'reference': (<MetricActor.DATASET_CHAR: 1>, 'Sheldon')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'

ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Harry'), 'reference': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Harry'), 'reference': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Harry')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Harry'), 'reference': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Joey')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could not be read! For query:
{'metric_name': 'bleu', 'metric_actors': {'predictor': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Harry'), 'reference': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Phoebe')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric 

...

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Sheldon')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Vader')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Common')}, 'metric_params': {}}
Skipping.
ERROR:root:Metric could n

ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'training_set': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Vader')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'training_set': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Base')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Barney')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! 

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'training_set': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Barney')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'training_set': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Bender')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'training_set': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Fry')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric ac

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metr

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'training_set': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Sheldon')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'training_set': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Vader')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'document': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'training_set': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Base')}, 'metric_params': {}}
Skipping.
ERROR:root:Invalid actor type for metric acto

In [17]:
metric = ('chatbot classifier', 'Chatbot Classifier', 'training_set', 'document')
print("Saving metric " + metric[1])
query = [{
    'metric_name': metric[0],
    'metric_actors': {
        metric[2]: (doc, char),
        metric[3]: (doc2, char2)
    },
    'metric_params': {
        'n_sentences': 75
    } 
} for doc in [MetricActor.DATASET_CHARCONTEXT, MetricActor.DATASET_CHAR, MetricActor.DIALOGPT_GREEDY,
              MetricActor.DIALOGPT_NBEAMS, MetricActor.DIALOGPT_SAMPLE]
  for char in ['Barney', 'Bender', 'Fry', 'Harry', 'Joey', 'Phoebe', 'Sheldon', 'Vader',
               'Common' if doc.value < 10 else 'Base']
  for doc2 in [MetricActor.DATASET_CHARCONTEXT, MetricActor.DATASET_CHAR, MetricActor.DIALOGPT_GREEDY,
              MetricActor.DIALOGPT_NBEAMS, MetricActor.DIALOGPT_SAMPLE]
  for char2 in ['Barney', 'Bender', 'Fry', 'Harry', 'Joey', 'Phoebe', 'Sheldon', 'Vader',
               'Common' if doc2.value < 10 else 'Base']]

answer = fetch_old_metrics(query)
logging.error("Found " + str(len(answer)) + " metrics for " + str(metric[1]))

for i in range(len(answer)):
    answer[i]['hash'] = dict_hash({key: answer[i][key] for key in ['metric_name',
                                                                   'metric_version',
                                                                   'metric_attempt',
                                                                   'metric_actors', 
                                                                   'context',
                                                                   'metric_params',
                                                                   'metric_samples']})
save_as_json(out_metrics_folder, metric[1], answer)

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry')}, 'metric_params': {'

ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Sheldon')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Vader')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Barney'), 'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Base')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric a

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Joey')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Phoebe')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Sheldon')}, 'metric_params': 

ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Bender')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Fry')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender'), 'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Harry')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric act

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Common')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry'), 'document': (<MetricActor.DATASET_CHAR: 1>, 'Barney')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry'), 'document': (<MetricActor.DATASET_CHAR: 1>, 'Bender')}, 'metric_params': {'n_sentences': 75}}
S

...

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Harry')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Joey')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Sheldon'), 'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Phoebe')}, 'metric_params': {'n_sentences': 7

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Bender')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Fry')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Harry')}, 'metric_params': {'n_sentences':

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'document': (<MetricActor.DIALOGPT_GREEDY: 10>, 'Base')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Barney')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Vader'), 'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Bender')}, 'metric_params': {'n_sentences': 75}}
S

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Sheldon')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Vader')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'document': (<MetricActor.DATASET_CHARCONTEXT: 0>, 'Common')}, 'metric_params': {'n_sentences'

ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Joey')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Phoebe')}, 'metric_params': {'n_sentences': 75}}
Skipping.
ERROR:root:Invalid actor type for metric actor 'training_set'!
ERROR:root:Metric could not be read! For query:
{'metric_name': 'chatbot classifier', 'metric_actors': {'training_set': (<MetricActor.DIALOGPT_SAMPLE: 12>, 'Base'), 'document': (<MetricActor.DIALOGPT_NBEAMS: 11>, 'Sheldon')}, 'metric_params': {'n_sentences': 75}}
Ski